In [16]:
# 2 loops
# Leave one out
# inner loops different parameters and algorithims
# which inner loop gives best

#pick classifier and window
#Classifiers: random forest, niave bayes, logistic regression (and different parameters)


#outer loop different people
#inner loop different algorithms, algorithm parameters and, window sizes, 

In [17]:
# Pandas for managing datasets
import pandas as pd

# Matplotlib for additional customization
from matplotlib import pyplot as plt
%matplotlib inline

# Seaborn for plotting and styling
import seaborn as sns

# Numpy and Random for math
import numpy as np
import random as rand

# Scikit Learn for Machine Learning
import sklearn
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import GaussianNB
from sklearn import metrics

# Itertools to combine lists
import itertools

In [18]:
def clean_dataset(df):
    assert isinstance(df, pd.DataFrame), "df needs to be a pd.DataFrame"
    df.dropna(inplace=True)
    indices_to_keep = ~df.isin([np.nan, np.inf, -np.inf]).any(1)
    return df[indices_to_keep].astype(np.float64)
data = pd.read_csv('Data\Windows.csv')
data = clean_dataset(data)
dataColumns = ['mg1','stdevg1','energyg1','mg2','stdevg2','energyg2','mg3','stdevg3','energyg3','ma1','stdeva1','energya1'
               ,'ma2','stdeva2','energya2','ma3','stdeva3','energya3',
               'g1g2','g1g3','g1a1','g1a2','g1a3','g2g3','g2a1','g2a2','g2a3','g3a1','g3a2','g3a3','a1a2','a1a3','a2a3']
windowSizes = [i for i in range(9, 90, 6)]
numPeople = 9
numClassifiers = 3
RFCValues = {"n_estimators": [1, 10, 100],
          "max_depth": [5, 10, 20, 50, 100, 200]}
RFCValues = [[1, 10, 100],
             [5, 10, 20, 50, 100, 200]]
LRValues = {"penalty": ['l1', 'l2'],
           "C": [0.01, 0.1, 0.2, 0.5, 0.7, 0.1, 1.1, 1.2, 1.5, 1.7, 1.2],
           "tol": [1e4, 1e3, 1e2, 1e1,1 , 1e-1, 1e-2, 1e-3, 1e-4],
           "solver":['newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga']}
LRValues = [['l1', 'l2'],
            [0.01, 0.1, 0.2, 0.5, 0.7, 0.1, 1.1, 1.2, 1.5, 1.7, 1.2],
            [1e4, 1e3, 1e2, 1e1,1 , 1e-1, 1e-2, 1e-3, 1e-4],
            ['liblinear', 'saga']]

#classifiers = [
#    RandomForestClassifier(),
#    GaussianNB(),
#    LogisticRegression()

In [9]:
'''
################
## Outer Loop ##
################

for i in range(0, numPeople):
    print 'i',i
    
    # Create the strings used for data separation
    string = '('
    string2 = ''
    for j in range(0, numPeople):
        if j != i:
            string += 'participantID=='+str(j)+' or '
            #if k < (len(items)-1):
            #    string += ' or '
        else:
            string2 += 'participantID=='+str(j)
    string = string[:-3] + ') and label!=1'
    string2 += ' and label!=1'
    
    # Use the strings to separate the data into training and testing
    trainDataValues = pd.DataFrame(data=data.query(string).filter(items=dataColumns+['windowSize']))
    trainLabels = pd.DataFrame(data=data.query(string).filter(items=['label','windowSize']))
    testDataValues = pd.DataFrame(data=data.query(string2).filter(items=dataColumns+['windowSize']))
    testLabels = pd.DataFrame(data=data.query(string2).filter(items=['label','windowSize']))
    
    ################
    ## Inner Loop ##
    ################
    
    # Loop through the number of classifiers 
    for j in range(0, numClassifiers):
        print 'j',j
        # If j == 0 use the RandomForestClassifier
        if j == 0:
            print 'j==0'
            # Use itertools.product to get all the possible combinations of parameters
            parameters = list(itertools.product(windowSizes, RFCValues[0], RFCValues[1]))
            # Loop through all the parameters
            for l in range(0, len(parameters)):
                print 'l',l
                # Create a string to filter window size
                string = 'windowSize=='+str(parameters[l][0])
                # Filter window size from all data
                trainDV = trainDataValues.query(string).filter(items=dataColumns)
                trainL = trainLabels.query(string).filter(items=['label'])
                testDV = testDataValues.query(string).filter(items=dataColumns)
                testL = testLabels.query(string).filter(items=['label'])
                # Create variables to store this loops parameters
                n_estimators = parameters[l][1]
                max_depth = parameters[l][2]

                # Create a RandomForestClassifier with this loops parameters
                clf = RandomForestClassifier(n_estimators=n_estimators, max_depth=max_depth, random_state=0)
                # Train the model
                clf.fit(trainDV, trainL)
                # Use the model
                predicted = clf.predict(testDV)
                # Get the accuracy
                accuracy = metrics.accuracy_score(np.ravel(testL),predicted)
                # Append that along with all the parameters to results
                results.write('RFC,'+str(parameters[l][0])+','+str(accuracy)+','+str(parameters[l][1])+','+str(parameters[l][2])+',None,None,'+str(i)+'\n')
        # If j == 1 use the GaussianNB classifier
        elif j == 1:
            print 'j==1'
            # Get parameters from windowSizes
            parameters = windowSizes
            # Loop through all the parameters
            for l in range(0, len(parameters)):
                print 'l',l
                string = 'windowSize=='+str(parameters[l])
                trainDV = trainDataValues.query(string).filter(items=dataColumns)
                trainL = trainLabels.query(string).filter(items=['label'])
                testDV = testDataValues.query(string).filter(items=dataColumns)
                testL = testLabels.query(string).filter(items=['label'])
                clf = GaussianNB()
                clf.fit(trainDV, trainL)
                predicted = clf.predict(testDV)
                accuracy = metrics.accuracy_score(np.ravel(testL),predicted)
                results.write('GNB,'+str(parameters[l])+','+str(accuracy)+',None,None,None,None,'+str(i)+'\n')
        # If j == 1 use the LogisticRegression classifier
        if j == 2:
            print 'j==2'
            # Use itertools.product to get all the possible combinations of parameters
            parameters = list(itertools.product(windowSizes, LRValues[0], LRValues[1], LRValues[2], LRValues[3]))
            # Loop through all the parameters
            for l in range(0, len(parameters)):
                print 'l',l
                string = 'windowSize=='+str(parameters[l][0])
                trainDV = trainDataValues.query(string).filter(items=dataColumns)
                trainL = trainLabels.query(string).filter(items=['label'])
                testDV = testDataValues.query(string).filter(items=dataColumns)
                testL = testLabels.query(string).filter(items=['label'])
                penalty = parameters[l][1]
                C = parameters[l][2]
                tol = parameters[l][3]
                solver = parameters[l][4]
                clf = LogisticRegression(penalty=penalty, C=C, tol=parameters[l][3], solver=solver)
                clf.fit(trainDV, trainL)
                predicted = clf.predict(testDV)
                accuracy = metrics.accuracy_score(np.ravel(testL),predicted)
                results.write('LR,'+str(parameters[l][0])+','+str(accuracy)+','+str(parameters[l][1])+','+str(parameters[l][2])+','+str(parameters[l][3])+','+str(parameters[l][4])+','+str(i)+'\n')
#dataFrame = pd.DataFrame(data=results)
#dataFrame.columns = ['Algorithm','windowSize', 'accuracy','param1','param2','param3','param4']
#dataFrame.to_csv('Data\Results.csv', sep=',', index=False)
'''

"\n################\n## Outer Loop ##\n################\n\nfor i in range(0, numPeople):\n    print 'i',i\n    \n    # Create the strings used for data separation\n    string = '('\n    string2 = ''\n    for j in range(0, numPeople):\n        if j != i:\n            string += 'participantID=='+str(j)+' or '\n            #if k < (len(items)-1):\n            #    string += ' or '\n        else:\n            string2 += 'participantID=='+str(j)\n    string = string[:-3] + ') and label!=1'\n    string2 += ' and label!=1'\n    \n    # Use the strings to separate the data into training and testing\n    trainDataValues = pd.DataFrame(data=data.query(string).filter(items=dataColumns+['windowSize']))\n    trainLabels = pd.DataFrame(data=data.query(string).filter(items=['label','windowSize']))\n    testDataValues = pd.DataFrame(data=data.query(string2).filter(items=dataColumns+['windowSize']))\n    testLabels = pd.DataFrame(data=data.query(string2).filter(items=['label','windowSize']))\n    \n   

In [20]:
results = open('Results\Results.csv', 'w')
results.write('Algorithm,windowSize,accuracy,param1,param2,param3,param4,innerLeftOut,outerLeftOut\n')
bestAlgs = open('Results\Best.csv', 'w')
bestAlgs.write('Algorithm,windowSize,accuracy,param1,param2,param3,param4,outerLeftOut\n')

In [48]:
################
## Outer Loop ##
################

for i in range(0,numPeople):
    print 'i',i
    
    ################
    ## Inner Loop ##
    ################
    
    for j in range(0,numPeople):
        if j!=i:
            print 'j',j
            string = '('
            string2 = ''
            for k in range(0,numPeople):
                if k!=i and k!=j:
                    string += 'participantID=='+str(k)+' or '
                    #if k < (len(items)-1):
                    #    string += ' or '
                elif k==j:
                    string2 += 'participantID=='+str(k)
            string = string[:-3] + ') and label!=1'
            string2 += ' and label!=1'
            print string
            print string2
            
            # Use the strings to separate the data into training and testing
            trainDataValues = pd.DataFrame(data=data).query(string).filter(items=dataColumns+['windowSize'])
            trainLabels = pd.DataFrame(data=data.query(string).filter(items=['label','windowSize']))
            testDataValues = pd.DataFrame(data=data).query(string2).filter(items=dataColumns+['windowSize'])
            testLabels = pd.DataFrame(data=data).query(string2).filter(items=['label','windowSize'])
            
            # Loop through the number of classifiers 
            for k in range(0, numClassifiers):
                print 'k',k
                # If k == 0 use the RandomForestClassifier
                if k == 0:
                    print 'k==0'
                    # Use itertools.product to get all the possible combinations of parameters
                    parameters = list(itertools.product(windowSizes, RFCValues[0], RFCValues[1]))
                    # Loop through all the parameters
                    for l in range(0, len(parameters)):
                        print 'l',l
                        # Create a string to filter window size
                        string = 'windowSize=='+str(parameters[l][0])
                        # Filter window size from all data
                        trainDV = trainDataValues.query(string).filter(items=dataColumns)
                        trainL = trainLabels.query(string).filter(items=['label'])
                        testDV = testDataValues.query(string).filter(items=dataColumns)
                        testL = testLabels.query(string).filter(items=['label'])
                        # Create variables to store this loops parameters
                        n_estimators = parameters[l][1]
                        max_depth = parameters[l][2]

                        # Create a RandomForestClassifier with this loops parameters
                        clf = RandomForestClassifier(n_estimators=n_estimators, max_depth=max_depth, random_state=0)
                        # Train the model
                        clf.fit(trainDV, np.ravel(trainL))
                        # Use the model
                        predicted = clf.predict(testDV)
                        # Get the accuracy
                        accuracy = metrics.accuracy_score(np.ravel(testL),predicted)
                        # Append that along with all the parameters to results
                        results.write('RFC,'+str(parameters[l][0])+','+str(accuracy)+','+str(parameters[l][1])+','+str(parameters[l][2])+',None,None,'+str(j)+','+str(i)+'\n')
                # If k == 1 use the GaussianNB classifier
                elif k == 1:
                    print 'k==1'
                    # Get parameters from windowSizes
                    parameters = windowSizes
                    # Loop through all the parameters
                    for l in range(0, len(parameters)):
                        print 'l',l
                        string = 'windowSize=='+str(parameters[l])
                        trainDV = trainDataValues.query(string).filter(items=dataColumns)
                        trainL = trainLabels.query(string).filter(items=['label'])
                        testDV = testDataValues.query(string).filter(items=dataColumns)
                        testL = testLabels.query(string).filter(items=['label'])
                        clf = GaussianNB()
                        clf.fit(trainDV, trainL)
                        predicted = clf.predict(testDV)
                        accuracy = metrics.accuracy_score(np.ravel(testL),predicted)
                        results.write('GNB,'+str(parameters[l])+','+str(accuracy)+',None,None,None,None,'+str(j)+','+str(i)+'\n')
                # If k == 2 use the LogisticRegression classifier
                if k == 2:
                    print 'k==2'
                    # Use itertools.product to get all the possible combinations of parameters
                    parameters = list(itertools.product(windowSizes, LRValues[0], LRValues[1], LRValues[2], LRValues[3]))
                    # Loop through all the parameters
                    for l in range(0, len(parameters)):
                        print 'l',l
                        string = 'windowSize=='+str(parameters[l][0])
                        trainDV = trainDataValues.query(string).filter(items=dataColumns)
                        trainL = trainLabels.query(string).filter(items=['label'])
                        testDV = testDataValues.query(string).filter(items=dataColumns)
                        testL = testLabels.query(string).filter(items=['label'])
                        penalty = parameters[l][1]
                        C = parameters[l][2]
                        tol = parameters[l][3]
                        solver = parameters[l][4]
                        clf = LogisticRegression(penalty=penalty, C=C, tol=parameters[l][3], solver=solver)
                        clf.fit(trainDV, trainL)
                        predicted = clf.predict(testDV)
                        accuracy = metrics.accuracy_score(np.ravel(testL),predicted)
                        results.write('LR,'+str(parameters[l][0])+','+str(accuracy)+','+str(parameters[l][1])+','+str(parameters[l][2])+','+str(parameters[l][3])+','+str(parameters[l][4])+','+str(j)+','+str(i)+'\n')
    '''
    result = pd.read_csv('Results\Results.csv').query('outerLeftOut=='+str(j))
    result['params']=result['param1'].map(str)+result['param2'].map(str)+result['param3'].map(str)+result['param4'].map(str)
    data_bestParams = result.groupby(['Algorithm','params'])['accuracy'].mean().reset_index()
    data_best = data[(data['Algorithm']=='GNB') | (data['Algorithm']=='LR') | (data['Algorithm']=='RFC')]
    data_best = data_best.groupby(['Algorithm','windowSize'])['accuracy'].mean().reset_index()
    data_best['windowSizeSeconds'] = (data_best['windowSize']/3)*200
    best = max(data_best.filter(items=['accuracy']))
    best_alg = data_best.query('accuracy=='+str(best))
    winSize = best_alg['windowSizeSeconds']
    alg = best_alg['Algorithm']
    param1 = best_alg['param1']
    param2 = best_alg['param2']
    param3 = best_alg['param3']
    param4 = best_alg['param4']
    accuracy = 0
    
    # Create the strings used for data separation
    string = '('
    string2 = ''
    for j in range(0, numPeople):
        if j != i:
            string += 'participantID=='+str(j)+' or '
            #if k < (len(items)-1):
            #    string += ' or '
        else:
            string2 += 'participantID=='+str(j)
    string = string[:-3] + ') and label!=1'
    string2 += ' and label!=1'
    
    # Use the strings to separate the data into training and testing
    trainDataValues = pd.DataFrame(data=data.query(string).filter(items=dataColumns+['windowSize']))
    trainLabels = pd.DataFrame(data=data.query(string).filter(items=['label','windowSize']))
    testDataValues = pd.DataFrame(data=data.query(string2).filter(items=dataColumns+['windowSize']))
    testLabels = pd.DataFrame(data=data.query(string2).filter(items=['label','windowSize']))
    
    if alg == 'RFC':
        clf = RandomForestClassifier(n_estimators=param1, max_depth=param2, random_state=0)
        clf.fit(trainDataValues, trainLabels)
        predicted = clf.predict(testDataValues)
        accuracy = metrics.accuracy_score(np.ravel(testLabels),predicted)
    elif alg == 'GNB':
        clf = GaussianNB()
        clf.fit(trainDataValues, trainLabels)
        predicted = clf.predict(testDataValues)
        accuracy = metrics.accuracy_score(np.ravel(testLabels),predicted)
    elif alg == 'LR':
        clf = LogisticRegression(penalty=param1, C=param2, tol=param3, solver=param4)
        clf.fit(trainDataValues, trainLabels)
        predicted = clf.predict(testDataValues)
        accuracy = metrics.accuracy_score(np.ravel(testLabels),predicted)
    bestAlg.write(str(alg)+','+str(winSize)+','+str(accuracy)+','+str(param1)+','+str(param2)+','+str(param3)+','+str(param4)+','+str(i)+'\n')
    '''

i 0
j 1
(participantID==2 or participantID==3 or participantID==4 or participantID==5 or participantID==6 or participantID==7 or participantID==8 ) and label!=1
participantID==1 and label!=1
k 0
k==0
l 0
l 1
l 2
l 3
l 4
l 5
l 6
l 7
l 8
l 9
l 10
l 11
l 12
l 13
l 14
l 15
l 16
l 17
l 18
l 19
l 20
l 21
l 22
l 23
l 24
l 25
l 26
l 27
l 28
l 29
l 30
l 31
l 32
l 33
l 34
l 35
l 36
l 37
l 38
l 39
l 40
l 41
l 42
l 43
l 44
l 45
l 46
l 47
l 48
l 49
l 50
l 51
l 52
l 53
l 54
l 55
l 56
l 57
l 58
l 59
l 60
l 61
l 62
l 63
l 64
l 65
l 66
l 67
l 68
l 69
l 70
l 71
l 72
l 73
l 74
l 75
l 76
l 77
l 78
l 79
l 80
l 81
l 82
l 83
l 84
l 85
l 86
l 87
l 88
l 89
l 90
l 91
l 92
l 93
l 94
l 95
l 96
l 97
l 98
l 99
l 100
l 101
l 102
l 103
l 104
l 105
l 106
l 107
l 108
l 109
l 110
l 111
l 112
l 113
l 114
l 115
l 116
l 117
l 118
l 119
l 120
l 121
l 122
l 123
l 124
l 125
l 126
l 127
l 128
l 129
l 130
l 131
l 132
l 133
l 134
l 135
l 136
l 137
l 138
l 139
l 140
l 141
l 142
l 143
l 144
l 145
l 146
l 147
l 148
l 149
l 150
l 15

l 1092
l 1093
l 1094
l 1095
l 1096
l 1097
l 1098
l 1099
l 1100
l 1101
l 1102
l 1103
l 1104
l 1105
l 1106
l 1107
l 1108
l 1109
l 1110
l 1111
l 1112
l 1113
l 1114
l 1115
l 1116
l 1117
l 1118
l 1119
l 1120
l 1121
l 1122
l 1123
l 1124
l 1125
l 1126
l 1127
l 1128
l 1129
l 1130
l 1131
l 1132
l 1133
l 1134
l 1135
l 1136
l 1137
l 1138
l 1139
l 1140
l 1141
l 1142
l 1143
l 1144
l 1145
l 1146
l 1147
l 1148
l 1149
l 1150
l 1151
l 1152
l 1153
l 1154
l 1155
l 1156
l 1157
l 1158
l 1159
l 1160
l 1161
l 1162
l 1163
l 1164
l 1165
l 1166
l 1167
l 1168
l 1169
l 1170
l 1171
l 1172
l 1173
l 1174
l 1175
l 1176
l 1177
l 1178
l 1179
l 1180
l 1181
l 1182
l 1183
l 1184
l 1185
l 1186
l 1187
l 1188
l 1189
l 1190
l 1191
l 1192
l 1193
l 1194
l 1195
l 1196
l 1197
l 1198
l 1199
l 1200
l 1201
l 1202
l 1203
l 1204
l 1205
l 1206
l 1207
l 1208
l 1209
l 1210
l 1211
l 1212
l 1213
l 1214
l 1215
l 1216
l 1217
l 1218
l 1219
l 1220
l 1221
l 1222
l 1223
l 1224
l 1225
l 1226
l 1227
l 1228
l 1229
l 1230
l 1231
l 1232
l 1233
l 1234

l 2264
l 2265
l 2266
l 2267
l 2268
l 2269
l 2270
l 2271
l 2272
l 2273
l 2274
l 2275
l 2276
l 2277
l 2278
l 2279
l 2280
l 2281
l 2282
l 2283
l 2284
l 2285
l 2286
l 2287
l 2288
l 2289
l 2290
l 2291
l 2292
l 2293
l 2294
l 2295
l 2296
l 2297
l 2298
l 2299
l 2300
l 2301
l 2302
l 2303
l 2304
l 2305
l 2306
l 2307
l 2308
l 2309
l 2310
l 2311
l 2312
l 2313
l 2314
l 2315
l 2316
l 2317
l 2318
l 2319
l 2320
l 2321
l 2322
l 2323
l 2324
l 2325
l 2326
l 2327
l 2328
l 2329
l 2330
l 2331
l 2332
l 2333
l 2334
l 2335
l 2336
l 2337
l 2338
l 2339
l 2340
l 2341
l 2342
l 2343
l 2344
l 2345
l 2346
l 2347
l 2348
l 2349
l 2350
l 2351
l 2352
l 2353
l 2354
l 2355
l 2356
l 2357
l 2358
l 2359
l 2360
l 2361
l 2362
l 2363
l 2364
l 2365
l 2366
l 2367
l 2368
l 2369
l 2370
l 2371
l 2372
l 2373
l 2374
l 2375
l 2376
l 2377
l 2378
l 2379
l 2380
l 2381
l 2382
l 2383
l 2384
l 2385
l 2386
l 2387
l 2388
l 2389
l 2390
l 2391
l 2392
l 2393
l 2394
l 2395
l 2396
l 2397
l 2398
l 2399
l 2400
l 2401
l 2402
l 2403
l 2404
l 2405
l 2406

l 3436
l 3437
l 3438
l 3439
l 3440
l 3441
l 3442
l 3443
l 3444
l 3445
l 3446
l 3447
l 3448
l 3449
l 3450
l 3451
l 3452
l 3453
l 3454
l 3455
l 3456
l 3457
l 3458
l 3459
l 3460
l 3461
l 3462
l 3463
l 3464
l 3465
l 3466
l 3467
l 3468
l 3469
l 3470
l 3471
l 3472
l 3473
l 3474
l 3475
l 3476
l 3477
l 3478
l 3479
l 3480
l 3481
l 3482
l 3483
l 3484
l 3485
l 3486
l 3487
l 3488
l 3489
l 3490
l 3491
l 3492
l 3493
l 3494
l 3495
l 3496
l 3497
l 3498
l 3499
l 3500
l 3501
l 3502
l 3503
l 3504
l 3505
l 3506
l 3507
l 3508
l 3509
l 3510
l 3511
l 3512
l 3513
l 3514
l 3515
l 3516
l 3517
l 3518
l 3519
l 3520
l 3521
l 3522
l 3523
l 3524
l 3525
l 3526
l 3527
l 3528
l 3529
l 3530
l 3531
l 3532
l 3533
l 3534
l 3535
l 3536
l 3537
l 3538
l 3539
l 3540
l 3541
l 3542
l 3543
l 3544
l 3545
l 3546
l 3547
l 3548
l 3549
l 3550
l 3551
l 3552
l 3553
l 3554
l 3555
l 3556
l 3557
l 3558
l 3559
l 3560
l 3561
l 3562
l 3563
l 3564
l 3565
l 3566
l 3567
l 3568
l 3569
l 3570
l 3571
l 3572
l 3573
l 3574
l 3575
l 3576
l 3577
l 3578

l 4608
l 4609
l 4610
l 4611
l 4612
l 4613
l 4614
l 4615
l 4616
l 4617
l 4618
l 4619
l 4620
l 4621
l 4622
l 4623
l 4624
l 4625
l 4626
l 4627
l 4628
l 4629
l 4630
l 4631
l 4632
l 4633
l 4634
l 4635
l 4636
l 4637
l 4638
l 4639
l 4640
l 4641
l 4642
l 4643
l 4644
l 4645
l 4646
l 4647
l 4648
l 4649
l 4650
l 4651
l 4652
l 4653
l 4654
l 4655
l 4656
l 4657
l 4658
l 4659
l 4660
l 4661
l 4662
l 4663
l 4664
l 4665
l 4666
l 4667
l 4668
l 4669
l 4670
l 4671
l 4672
l 4673
l 4674
l 4675
l 4676
l 4677
l 4678
l 4679
l 4680
l 4681
l 4682
l 4683
l 4684
l 4685
l 4686
l 4687
l 4688
l 4689
l 4690
l 4691
l 4692
l 4693
l 4694
l 4695
l 4696
l 4697
l 4698
l 4699
l 4700
l 4701
l 4702
l 4703
l 4704
l 4705
l 4706
l 4707
l 4708
l 4709
l 4710
l 4711
l 4712
l 4713
l 4714
l 4715
l 4716
l 4717
l 4718
l 4719
l 4720
l 4721
l 4722
l 4723
l 4724
l 4725
l 4726
l 4727
l 4728
l 4729
l 4730
l 4731
l 4732
l 4733
l 4734
l 4735
l 4736
l 4737
l 4738
l 4739
l 4740
l 4741
l 4742
l 4743
l 4744
l 4745
l 4746
l 4747
l 4748
l 4749
l 4750

...

l 242
l 243
l 244
l 245
l 246
l 247
l 248
l 249
l 250
l 251
l 252
l 253
l 254
l 255
l 256
l 257
l 258
l 259
l 260
l 261
l 262
l 263
l 264
l 265
l 266
l 267
l 268
l 269
l 270
l 271
l 272
l 273
l 274
l 275
l 276
l 277
l 278
l 279
l 280
l 281
l 282
l 283
l 284
l 285
l 286
l 287
l 288
l 289
l 290
l 291
l 292
l 293
l 294
l 295
l 296
l 297
l 298
l 299
l 300
l 301
l 302
l 303
l 304
l 305
l 306
l 307
l 308
l 309
l 310
l 311
l 312
l 313
l 314
l 315
l 316
l 317
l 318
l 319
l 320
l 321
l 322
l 323
l 324
l 325
l 326
l 327
l 328
l 329
l 330
l 331
l 332
l 333
l 334
l 335
l 336
l 337
l 338
l 339
l 340
l 341
l 342
l 343
l 344
l 345
l 346
l 347
l 348
l 349
l 350
l 351
l 352
l 353
l 354
l 355
l 356
l 357
l 358
l 359
l 360
l 361
l 362
l 363
l 364
l 365
l 366
l 367
l 368
l 369
l 370
l 371
l 372
l 373
l 374
l 375
l 376
l 377
l 378
l 379
l 380
l 381
l 382
l 383
l 384
l 385
l 386
l 387
l 388
l 389
l 390
l 391
l 392
l 393
l 394
l 395
l 396
l 397
l 398
l 399
l 400
l 401
l 402
l 403
l 404
l 405
l 406
l 407
l 40

l 1523
l 1524
l 1525
l 1526
l 1527
l 1528
l 1529
l 1530
l 1531
l 1532
l 1533
l 1534
l 1535
l 1536
l 1537
l 1538
l 1539
l 1540
l 1541
l 1542
l 1543
l 1544
l 1545
l 1546
l 1547
l 1548
l 1549
l 1550
l 1551
l 1552
l 1553
l 1554
l 1555
l 1556
l 1557
l 1558
l 1559
l 1560
l 1561
l 1562
l 1563
l 1564
l 1565
l 1566
l 1567
l 1568
l 1569
l 1570
l 1571
l 1572
l 1573
l 1574
l 1575
l 1576
l 1577
l 1578
l 1579
l 1580
l 1581
l 1582
l 1583
l 1584
l 1585
l 1586
l 1587
l 1588
l 1589
l 1590
l 1591
l 1592
l 1593
l 1594
l 1595
l 1596
l 1597
l 1598
l 1599
l 1600
l 1601
l 1602
l 1603
l 1604
l 1605
l 1606
l 1607
l 1608
l 1609
l 1610
l 1611
l 1612
l 1613
l 1614
l 1615
l 1616
l 1617
l 1618
l 1619
l 1620
l 1621
l 1622
l 1623
l 1624
l 1625
l 1626
l 1627
l 1628
l 1629
l 1630
l 1631
l 1632
l 1633
l 1634
l 1635
l 1636
l 1637
l 1638
l 1639
l 1640
l 1641
l 1642
l 1643
l 1644
l 1645
l 1646
l 1647
l 1648
l 1649
l 1650
l 1651
l 1652
l 1653
l 1654
l 1655
l 1656
l 1657
l 1658
l 1659
l 1660
l 1661
l 1662
l 1663
l 1664
l 1665

l 2696
l 2697
l 2698
l 2699
l 2700
l 2701
l 2702
l 2703
l 2704
l 2705
l 2706
l 2707
l 2708
l 2709
l 2710
l 2711
l 2712
l 2713
l 2714
l 2715
l 2716
l 2717
l 2718
l 2719
l 2720
l 2721
l 2722
l 2723
l 2724
l 2725
l 2726
l 2727
l 2728
l 2729
l 2730
l 2731
l 2732
l 2733
l 2734
l 2735
l 2736
l 2737
l 2738
l 2739
l 2740
l 2741
l 2742
l 2743
l 2744
l 2745
l 2746
l 2747
l 2748
l 2749
l 2750
l 2751
l 2752
l 2753
l 2754
l 2755
l 2756
l 2757
l 2758
l 2759
l 2760
l 2761
l 2762
l 2763
l 2764
l 2765
l 2766
l 2767
l 2768
l 2769
l 2770
l 2771
l 2772
l 2773
l 2774
l 2775
l 2776
l 2777
l 2778
l 2779
l 2780
l 2781
l 2782
l 2783
l 2784
l 2785
l 2786
l 2787
l 2788
l 2789
l 2790
l 2791
l 2792
l 2793
l 2794
l 2795
l 2796
l 2797
l 2798
l 2799
l 2800
l 2801
l 2802
l 2803
l 2804
l 2805
l 2806
l 2807
l 2808
l 2809
l 2810
l 2811
l 2812
l 2813
l 2814
l 2815
l 2816
l 2817
l 2818
l 2819
l 2820
l 2821
l 2822
l 2823
l 2824
l 2825
l 2826
l 2827
l 2828
l 2829
l 2830
l 2831
l 2832
l 2833
l 2834
l 2835
l 2836
l 2837
l 2838

l 3868
l 3869
l 3870
l 3871
l 3872
l 3873
l 3874
l 3875
l 3876
l 3877
l 3878
l 3879
l 3880
l 3881
l 3882
l 3883
l 3884
l 3885
l 3886
l 3887
l 3888
l 3889
l 3890
l 3891
l 3892
l 3893
l 3894
l 3895
l 3896
l 3897
l 3898
l 3899
l 3900
l 3901
l 3902
l 3903
l 3904
l 3905
l 3906
l 3907
l 3908
l 3909
l 3910
l 3911
l 3912
l 3913
l 3914
l 3915
l 3916
l 3917
l 3918
l 3919
l 3920
l 3921
l 3922
l 3923
l 3924
l 3925
l 3926
l 3927
l 3928
l 3929
l 3930
l 3931
l 3932
l 3933
l 3934
l 3935
l 3936
l 3937
l 3938
l 3939
l 3940
l 3941
l 3942
l 3943
l 3944
l 3945
l 3946
l 3947
l 3948
l 3949
l 3950
l 3951
l 3952
l 3953
l 3954
l 3955
l 3956
l 3957
l 3958
l 3959
l 3960
l 3961
l 3962
l 3963
l 3964
l 3965
l 3966
l 3967
l 3968
l 3969
l 3970
l 3971
l 3972
l 3973
l 3974
l 3975
l 3976
l 3977
l 3978
l 3979
l 3980
l 3981
l 3982
l 3983
l 3984
l 3985
l 3986
l 3987
l 3988
l 3989
l 3990
l 3991
l 3992
l 3993
l 3994
l 3995
l 3996
l 3997
l 3998
l 3999
l 4000
l 4001
l 4002
l 4003
l 4004
l 4005
l 4006
l 4007
l 4008
l 4009
l 4010

l 5040
l 5041
l 5042
l 5043
l 5044
l 5045
l 5046
l 5047
l 5048
l 5049
l 5050
l 5051
l 5052
l 5053
l 5054
l 5055
l 5056
l 5057
l 5058
l 5059
l 5060
l 5061
l 5062
l 5063
l 5064
l 5065
l 5066
l 5067
l 5068
l 5069
l 5070
l 5071
l 5072
l 5073
l 5074
l 5075
l 5076
l 5077
l 5078
l 5079
l 5080
l 5081
l 5082
l 5083
l 5084
l 5085
l 5086
l 5087
l 5088
l 5089
l 5090
l 5091
l 5092
l 5093
l 5094
l 5095
l 5096
l 5097
l 5098
l 5099
l 5100
l 5101
l 5102
l 5103
l 5104
l 5105
l 5106
l 5107
l 5108
l 5109
l 5110
l 5111
l 5112
l 5113
l 5114
l 5115
l 5116
l 5117
l 5118
l 5119
l 5120
l 5121
l 5122
l 5123
l 5124
l 5125
l 5126
l 5127
l 5128
l 5129
l 5130
l 5131
l 5132
l 5133
l 5134
l 5135
l 5136
l 5137
l 5138
l 5139
l 5140
l 5141
l 5142
l 5143
l 5144
l 5145
l 5146
l 5147
l 5148
l 5149
l 5150
l 5151
l 5152
l 5153
l 5154
l 5155
l 5156
l 5157
l 5158
l 5159
l 5160
l 5161
l 5162
l 5163
l 5164
l 5165
l 5166
l 5167
l 5168
l 5169
l 5170
l 5171
l 5172
l 5173
l 5174
l 5175
l 5176
l 5177
l 5178
l 5179
l 5180
l 5181
l 5182

In [131]:
result = pd.read_csv('Results\Results.csv')#.query('outerLeftOut=='+str(j))
result['params']=result['param1'].map(str)+result['param2'].map(str)+result['param3'].map(str)+result['param4'].map(str)
result.head()

Algorithm  windowSize  accuracy param1 param2 param3 param4  innerLeftOut  \
0       RFC           9  0.533270      1      5   None   None           1.0   
1       RFC           9  0.758080      1     10   None   None           1.0   
2       RFC           9  0.762833      1     20   None   None           1.0   
3       RFC           9  0.752376      1     50   None   None           1.0   
4       RFC           9  0.752376      1    100   None   None           1.0   

   outerLeftOut        params  
0           0.0    15NoneNone  
1           0.0   110NoneNone  
2           0.0   120NoneNone  
3           0.0   150NoneNone  
4           0.0  1100NoneNone

In [155]:
result_outer = result.groupby(['outerLeftOut','Algorithm','params','windowSize'])['accuracy'].mean().reset_index()

In [157]:
idx = result_outer.groupby(['outerLeftOut'])['accuracy'].transform(max) == result_outer['accuracy']

In [160]:
result_outer_final = result_outer[idx]

In [164]:
result_outer_final[result_outer_final['windowSize'] == 63]

outerLeftOut Algorithm          params  windowSize  accuracy
4629            0.0       RFC    1005NoneNone          63  0.959600
9361            1.0       RFC  100100NoneNone          63  0.985712
9389            1.0       RFC  100200NoneNone          63  0.985712
9403            1.0       RFC   10020NoneNone          63  0.985712
9417            1.0       RFC   10050NoneNone          63  0.985712
23767           4.0       RFC  100100NoneNone          63  0.961606
23795           4.0       RFC  100200NoneNone          63  0.961606
23809           4.0       RFC   10020NoneNone          63  0.961606
23823           4.0       RFC   10050NoneNone          63  0.961606
23837           4.0       RFC    1005NoneNone          63  0.961606
28639           5.0       RFC    1005NoneNone          63  0.959409

In [165]:
result_outer_final[result_outer_final['windowSize'] == 63].groupby(['params'])['outerLeftOut'].count()

params
100100NoneNone    2
100200NoneNone    2
10020NoneNone     2
10050NoneNone     2
1005NoneNone      3
Name: outerLeftOut, dtype: int64

In [169]:
best_results = result_outer[(result_outer['windowSize'] == 63) & (result_outer['params'] == '1005NoneNone') & (result_outer['Algorithm'] == 'RFC')]

In [170]:
best_results['accuracy'].mean()

0.96305432683006942

In [133]:
#data_best = data[((data['Algorithm']=='GNB') & (data['params']=='NoneNoneNoneNone')) | ((data['Algorithm']=='LR') & (data['params']=='l10.010.0001liblinear')) | ((data['Algorithm']=='RFC') & (data['params']=='1005NoneNone'))]
data_best = result.groupby(['Algorithm','windowSize','param1','param2','param3','param4','outerLeftOut'])['accuracy'].mean().reset_index()
data_best.head()
best_alg = data_best.max()
print best_alg

Algorithm            RFC
windowSize            87
param1                l2
param2              None
param3              None
param4              saga
outerLeftOut           8
accuracy        0.985712
dtype: object


In [112]:
winSize = best_alg['windowSize']
alg = best_alg['Algorithm']
print alg
param1 = best_alg['param1']
print param1
param2 = best_alg['param2']
print param2
param3 = best_alg['param3']
print param3
param4 = best_alg['param4']
print param4
accuracy = 0

# Create the strings used for data separation
for i in range(0, numPeople):    
    string = '('
    string2 = ''
    for j in range(0, numPeople):
        if j != i:
            string += 'participantID=='+str(j)+' or '
            #if k < (len(items)-1):
            #    string += ' or '
        else:
            string2 += 'participantID=='+str(j)

    string = string[:-3] + ') and windowSize=='+str(winSize)+' and label!=1'
    string2 += ' and windowSize=='+str(winSize)+' and label!=1'
    
    # Use the strings to separate the data into training and testing
    trainDataValues = pd.DataFrame(data=data.query(string).filter(items=dataColumns))
    trainLabels = pd.DataFrame(data=data.query(string).filter(items=['label']))
    testDataValues = pd.DataFrame(data=data.query(string2).filter(items=dataColumns))
    testLabels = pd.DataFrame(data=data.query(string2).filter(items=['label']))
    #print trainDataValues
    
    if alg == 'RFC':
        clf = RandomForestClassifier(n_estimators=int(param1), max_depth=param2, random_state=0)
        clf.fit(trainDataValues, trainLabels)
        predicted = clf.predict(testDataValues)
        accuracy = metrics.accuracy_score(np.ravel(testLabels),predicted)
    elif alg == 'GNB':
        clf = GaussianNB()
        clf.fit(trainDataValues, trainLabels)
        predicted = clf.predict(testDataValues)
        accuracy = metrics.accuracy_score(np.ravel(testLabels),predicted)
    elif alg == 'LR':
        clf = LogisticRegression(penalty=param1, C=param2, tol=param3, solver=param4)
        clf.fit(trainDataValues, trainLabels)
        predicted = clf.predict(testDataValues)
        accuracy = metrics.accuracy_score(np.ravel(testLabels),predicted)

RFC
l2
None
None
saga


ValueError: invalid literal for int() with base 10: 'l2'